# Graphical Notebook

In [132]:
#standard import 
import numpy as np
import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
from matplotlib import animation
from matplotlib.animation import PillowWriter
from matplotlib.animation import FuncAnimation
from IPython import display
from IPython.display import HTML
import seaborn as sns
import shapefile as shpa
import geopandas as gpd
import os
import ffmpeg

In [392]:
#checking working directory to save graphs for flask app
os.getcwd()

'/Users/kellykai'

## Importing databases with ML popoulated is_fishing

In [343]:
ak_eez = pd.read_csv('ak.csv')
westcoast_eez = pd.read_csv('westcoast.csv')
hi_eez = pd.read_csv('hi.csv')

In [348]:
#counting number of unique boats
mmsi = []
databases = [ak_eez,westcoast_eez,hi_eez]
for j in range(len(databases)):
    for i in range(len(databases[j])):
        if databases[j].mmsi[i] not in mmsi:
            mmsi.append(databases[j].mmsi[i])
len(mmsi)

33

In [349]:
#counting instances for each unique boat 
mmsi_dict = {}
for i in range(len(mmsi)):
    for j in range(len(databases)):
        if mmsi[i] in list(databases[j].mmsi):
            mmsi_dict[mmsi[i]] = list(databases[j].mmsi).count(mmsi[i])
mmsi_dict
        

{1252339803566.0: 1,
 51101297206144.0: 2,
 121426486551523.0: 1,
 192426881471378.0: 2,
 39859406485734.0: 1,
 86817739143879.0: 257,
 79111403404442.0: 2379,
 103786638076601.0: 1,
 261683006747890.0: 1,
 51394439323066.0: 125519,
 103576446797335.0: 618,
 168015789077263.0: 81,
 33266086194351.0: 36,
 118281075999064.0: 35301,
 259600076146315.0: 1896,
 103998194181708.0: 728,
 131404935810738.0: 68401,
 130481650671667.0: 1,
 229675783400528.0: 96941,
 125954407820672.0: 10040,
 103912281609040.0: 2,
 143906914639303.0: 30,
 118485905119293.0: 7260,
 182087889708399.0: 3798,
 77832927010710.0: 823,
 95062718521348.0: 252,
 109864465509954.0: 275,
 204349732031005.0: 1,
 229926462784947.0: 644,
 251022003811177.0: 387,
 262534508730959.0: 144,
 263392518194890.0: 3023,
 89470223580135.0: 187}

In [350]:
#create a list of boats with less than 100 instances
drop_list = []
for i in mmsi:
    if mmsi_dict[i] < 100:
        drop_list.append(i)     

In [ ]:
#dropping all of the rows from each databases with less than 100 instances
for i in range(len(drop_list)):
    if drop_list[i] in list(ak_eez.mmsi):
        ak_eez = ak_eez[ak_eez.mmsi != drop_list[i]]
    ak_eez = ak_eez.reset_index(drop = True)
    if drop_list[i] in list(westcoast_eez.mmsi):
        westcoast_eez = westcoast_eez[westcoast_eez.mmsi != drop_list[i]]
    westcoast_eez = westcoast_eez.reset_index(drop = True)
    if drop_list[i] in list(hi_eez.mmsi):
        hi_eez = hi_eez[hi_eez.mmsi != drop_list[i]]
    hi_eez = hi_eez.reset_index(drop = True)


# WEST COAST EEZ

## Adding is suspicious column to each data frame by region


In [69]:
#westcoast restricted areas
cape_flacon_coord = {'lat': (45.44,45.48), 'lon': (-124.035,-123.5677)}
cascade_head_coord = {'lat':(44.5650,45.05),'lon':( -124.050,-124.0040)}
otter_rock_coord = {'lat':(44.4331, 44.4517),'lon':(-124.0453,-124.0366)}
cape_perpetua_coor = {'lat':(44.0575,44.200),'lon':(-124.1100,-124.0673)}
redfish_rocks = {'lat':(42.4025,42.4296),'lon':(-124.3250,-124.2718)}

#creating list of suspicious indices
sus_oregon = []
for i in range(len(westcoast_eez)):
    if 45.44<westcoast_eez.lat[i]<45.48 and -124.035<westcoast_eez.lon[i]<-123.5677:
        sus_oregon.append(i)
    elif 44.5650<westcoast_eez.lat[i]<45.05 and -124.05<westcoast_eez.lon[i]<-124.0040:
        sus_oregon.append(i)
    elif 44.4331<westcoast_eez.lat[i]<44.4517 and -124.0453<westcoast_eez.lon[i]<-124.0366:
        sus_oregon.append(i)
    elif 44.0575<westcoast_eez.lat[i]<44.200 and -124.1100<westcoast_eez.lon[i]<-124.0673:
        sus_oregon.append(i)
    elif 42.4025<westcoast_eez.lat[i]<42.4296 and -124.3250<westcoast_eez.lon[i]<-124.2718:
        sus_oregon.append(i)

#creating list of suspicious indices and adding to dataframe         
is_suspicious = []        
for i in range(len(westcoast_eez)):
    if i in sus_oregon:
        is_suspicious.append(1)
    else:
        is_suspicious.append(0)

westcoast_eez['is_suspicious'] = is_suspicious

In [143]:
#count to check for any is_suspicious and is_fishing instances
indices = []
for i in range(len(westcoast_eez)):
    if westcoast_eez.is_suspicious[i] == 1 and westcoast_eez.is_fishing[i] == 1:
        indices.append(i)
westcoast_eez.iloc[indices]

mmsi     timestamp  distance_from_shore  distance_from_port  \
1829   1.259544e+14  1.459461e+09             0.000000         1414.178833   
1831   1.259544e+14  1.459462e+09             0.000000         1414.178833   
1883   1.259544e+14  1.459875e+09             0.000000          999.975464   
14390  2.296758e+14  1.373773e+09          3162.200195        38117.300781   

       speed      course        lat         lon  is_fishing source gear_type  \
1829     0.3   59.299999  44.629807 -124.042465         1.0    gfw  trollers   
1831     0.5   24.500000  44.630432 -124.041977         1.0    gfw  trollers   
1883     0.3  296.100006  44.631443 -124.045639         1.0    gfw  trollers   
14390    5.4  352.000000  45.047115 -124.041496         1.0    gfw   unknown   

       is_suspicious  
1829               1  
1831               1  
1883               1  
14390              1

## Splitting dataframes into unique boats for plotting

In [ ]:
#splitting westcoast datframe by unique boat 
mmsi = []
for i in range(len(hi_eez)):
    if hi_eez.mmsi[i] not in mmsi:
        mmsi.append(hi_eez.mmsi[i])
  

In [ ]:
#split west coast dataframe by boat
wc_boat1, wc_boat2, wc_boat3 = [x for _, x in westcoast_eez.groupby(westcoast_eez['mmsi'])]
wc_boat1.reset_index(drop = True, inplace = True)
wc_boat2.reset_index(drop = True, inplace = True)
wc_boat3.reset_index(drop = True, inplace = True)

In [394]:
#making list of westcaost boats for the loop below 
wc_boats = [wc_boat1, wc_boat2, wc_boat3]
for i in range(len(wc_boats)):
    print(len(wc_boats[i]))

257
9112
45261


In [235]:
#wc_boat 3 is too long, too much port time, lets remove 
#if you want to remove port data 
port_list = []
for i in range(len(wc_boat3)):
    if wc_boat3.distance_from_shore[i] == 0.0 and wc_boat3.speed[i] == 0.0:
        port_list.append(i)
wc_boat3.drop(port_list, inplace = True)

port_list = []
for i in range(len(wc_boat2)):
    if wc_boat2.distance_from_shore[i] == 0 and wc_boat2.speed[i] == 0.0:
        port_list.append(i)
wc_boat2.drop(port_list, inplace = True)

port_list = []
for i in range(len(wc_boat1)):
    if wc_boat1.distance_from_shore[i] == 0 and wc_boat1.speed[i] == 0.0:
        port_list.append(i)
wc_boat1.drop(port_list, inplace = True)
#reset all indices 
wc_boat1.reset_index(drop = True, inplace = True)
wc_boat2.reset_index(drop = True, inplace = True)
wc_boat3.reset_index(drop = True, inplace = True)

In [387]:
#just fishing instances 
for i in range(len(wc_boats)):
    indicies = []
    for j in range(len(wc_boats[i])):
        if wc_boats[i].is_fishing[j] == 1:
            indicies.append(j)
    print(len(indicies))

54
4425
22104


In [391]:
#count to check for any is_suspicious and is_fishing instances

for i in range(len(wc_boats)):
    indicies = []
    for j in range(len(wc_boats[i])):
        if wc_boats[i].is_suspicious[j] == 1 and wc_boats[i].is_fishing[j] == 1:
            indicies.append(j)
    print(len(indicies))

0
3
1


## Graphing how we want final to look 


In [239]:
for i in range(len(wc_boats)): 
    #l=[1]
    if wc_boats[i] is wc_boat1:
        frames = 257
        adj = 1
        f = r'/Users/kellykai/Desktop/Flask_app/Static/wcboat1.mp4'
        color = 'blue'
    if wc_boats[i] is wc_boat2:
        frames = 1000
        adj = 9
        f = r'/Users/kellykai/Desktop/Flask_app/Static/wcboat2.mp4'
        color = 'blue'
        
    if wc_boats[i] is wc_boat3:
        frames = 5000
        adj = 9
        f = r'/Users/kellykai/Desktop/Flask_app/Static/wcboat3.mp4'
        color = 'blue'
        
        

        
    x = list(wc_boats[i].lon)
    fig, ax = plt.subplots(figsize=(8,6))
    #fig = plt.figure()
    #l = [1]
    
    lines = plt.plot([],'o', c = color)
    line = lines[0]
    

    #other setup 
    countries = gpd.read_file(  
         gpd.datasets.get_path("naturalearth_lowres"))
    countries[countries["name"] == "United States of America"].plot(color='#0B7530',
                                                     ax=ax)
    countries[countries["name"] == "Canada"].plot(color='#0B7530',
                                                     ax=ax)
    countries[countries["name"] == "Mexico"].plot(color='#0B7530',
                                                     ax=ax)
    ax.grid(b=True, alpha=0.5)
    plt.axis([-130, -115, 30, 50])

    #animate
    def animate(frame):
        #update plot 
        #l.append(int(frame*adj))
        
        y = list(wc_boats[i].lat)[int(frame*adj)]
        line.set_data((x[int(frame*adj)],y))
        if wc_boats[i] is wc_boat2 and 1800<int(frame*adj)<1900:
            line.set_color('red')
        elif wc_boats[i].is_fishing[frame*adj] != 0:
            line.set_color('green')
        else:
            line.set_color('blue')

    anim = FuncAnimation(fig, animate, frames = frames, interval = 20)
    video = anim.to_html5_video()
    html = display.HTML(video)
    display.display(html)
    writervideo = animation.FFMpegWriter(fps=60) 
    anim.save(f, writer=writervideo)
    plt.close()
    

# HAWAII

In [242]:
#hawaiian marine reserve papahanaumokukaea 
papahanaumokukaea_coord = {'lat': (22.22343,29.25614), 'lon': (-179.27432,-161.0173)}

#list of suspicipous indices 
sus_hi = []
for i in range(len(hi_eez)):
    if 22.22343<hi_eez.lat[i]<29.25614 and -179.27432<hi_eez.lon[i]<-161.0173:
        sus_hi.append(i)
len(sus_hi)

#creating list of suspicious indices and adding to dataframe         
is_suspicious = []        
for i in range(len(hi_eez)):
    if i in sus_hi:
        is_suspicious.append(1)
    else:
        is_suspicious.append(0)

hi_eez['is_suspicious'] = is_suspicious

In [243]:
#count to check for any is_suspicious and is_fishing instances
indices = []
for i in range(len(hi_eez)):
    if hi_eez.is_suspicious[i] == 1 and hi_eez.is_fishing[i] == 1:
        indices.append(i)
hi_eez.iloc[indices]

mmsi     timestamp  distance_from_shore  distance_from_port  \
13769  2.633925e+14  1.390379e+09        739669.625000       843081.312500   
13772  2.633925e+14  1.390381e+09        740581.562500       843188.062500   
13773  2.633925e+14  1.390381e+09        740498.562500       842537.312500   
13774  2.633925e+14  1.390381e+09        740498.562500       842537.312500   
13775  2.633925e+14  1.390385e+09        745014.625000       842469.062500   
...             ...           ...                  ...                 ...   
16367  2.633925e+14  1.478519e+09        140117.937500       145450.906250   
16368  2.633925e+14  1.478519e+09        140797.828125       146099.125000   
16369  2.633925e+14  1.478519e+09        141481.515625       146751.296875   
16373  2.633925e+14  1.478520e+09        142168.937500       147407.375000   
16386  2.633925e+14  1.478545e+09        230784.281250       233474.468750   

       speed      course        lat         lon  is_fishing         source  \
13769    1.6  337.700012  29.011580 -161.349243         1.0  crowd_sourced   
13772    4.3  305.399994  29.018517 -161.361694         1.0  crowd_sourced   
13773    3.9  297.200012  29.018850 -161.362274         1.0  crowd_sourced   
13774    5.5  304.399994  29.019167 -161.362930         1.0  crowd_sourced   
13775    5.0  329.399994  29.054159 -161.421021         1.0  crowd_sourced   
...      ...         ...        ...         ...         ...            ...   
16367    7.6  349.700012  24.644032 -165.292236         1.0  crowd_sourced   
16368    6.5    1.200000  24.644983 -165.292252         1.0  crowd_sourced   
16369    6.8   12.200000  24.655724 -165.292603         1.0  crowd_sourced   
16373    6.3    4.600000  24.664459 -165.292892         1.0  crowd_sourced   
16386    6.5    5.300000  25.559055 -165.316193         1.0  crowd_sourced   

       gear_type  is_suspicious  
13769  longlines              1  
13772  longlines              1  
13773  longlines              1  
13774  longlines              1  
13775  longlines              1  
...          ...            ...  
16367  longlines              1  
16368  longlines              1  
16369  longlines              1  
16373  longlines              1  
16386  longlines              1  

[126 rows x 12 columns]

In [244]:
#splitting hawaii datframe by unique boat 
mmsi = []
for i in range(len(hi_eez)):
    if hi_eez.mmsi[i] not in mmsi:
        mmsi.append(hi_eez.mmsi[i])
len(mmsi)      

10

In [253]:
#split west coast dataframe by boat
hi_boat1, hi_boat2, hi_boat3,hi_boat4, hi_boat5, hi_boat6, hi_boat7, hi_boat8, hi_boat9, hi_boat10 = [x for _, x in hi_eez.groupby(hi_eez['mmsi'])]
hi_boat1.reset_index(drop = True, inplace = True)
hi_boat2.reset_index(drop = True, inplace = True)
hi_boat3.reset_index(drop = True, inplace = True)
hi_boat4.reset_index(drop = True, inplace = True)
hi_boat5.reset_index(drop = True, inplace = True)
hi_boat6.reset_index(drop = True, inplace = True)
hi_boat7.reset_index(drop = True, inplace = True)
hi_boat8.reset_index(drop = True, inplace = True)
hi_boat9.reset_index(drop = True, inplace = True)
hi_boat10.reset_index(drop = True, inplace = True)
#making a list of the dataframes 
hi_boats = [hi_boat1, hi_boat2, hi_boat3,hi_boat4, hi_boat5, hi_boat6, hi_boat7, hi_boat8, hi_boat9, hi_boat10]

#checking length to see if any are too long and need to remove port 
lens = []
for i in range(len(hi_boats)):
    lens.append(len(hi_boats[i]))
# all are fine, will leave port instances 
lens

[823, 187, 252, 275, 7260, 3798, 644, 387, 144, 3023]

In [385]:
#count to check for any is_suspicious and is_fishing instances

for i in range(len(hi_boats)):
    indicies = []
    for j in range(len(hi_boats[i])):
        if hi_boats[i].is_suspicious[j] == 1 and hi_boats[i].is_fishing[j] == 1:
            indicies.append(j)
    print(len(indicies))
#only boat 10 has instances of both

0
0
0
0
0
0
0
0
0
126


In [384]:
#just fishing 
for i in range(len(hi_boats)):
    indicies = []
    for j in range(len(hi_boats[i])):
        if hi_boats[i].is_fishing[j] == 1:
            indicies.append(j)
    print(len(indicies))

26
0
0
0
1058
0
9
0
0
643


In [ ]:
#plotting 
#lengths = [823, 187, 252, 275, 7260, 3798, 644, 387, 144, 3023]
for i in range(len(hi_boats)): 
    #l=[1]
    if hi_boats[i] is hi_boat1:
        frames = 823
        adj = 1
        f = r'/Users/kellykai/Desktop/Flask_app/Static/hiboat1.mp4'
        color = 'blue'
    if hi_boats[i] is hi_boat2:
        frames = 187
        adj = 1
        f = r'/Users/kellykai/Desktop/Flask_app/Static/hiboat2.mp4'
        color = 'blue'
        
    if hi_boats[i] is hi_boat3:
        frames = 252
        adj = 1
        f = r'/Users/kellykai/Desktop/Flask_app/Static/hiboat3.mp4'
        color = 'blue'
    if hi_boats[i] is hi_boat4:
        frames = 275
        adj = 1
        f = r'/Users/kellykai/Desktop/Flask_app/Static/hiboat4.mp4'
        color = 'blue'
    if hi_boats[i] is hi_boat5:
        frames = 2400
        adj = 3
        f = r'/Users/kellykai/Desktop/Flask_app/Static/hiboat5.mp4'
        color = 'blue'
        
    if hi_boats[i] is hi_boat6:
        frames = 1899
        adj = 2
        f = r'/Users/kellykai/Desktop/Flask_app/Static/hiboat6.mp4'
        color = 'blue'
    if hi_boats[i] is hi_boat7:
        frames = 644
        adj = 1
        f = r'/Users/kellykai/Desktop/Flask_app/Static/hiboat7.mp4'
        color = 'blue'
    if hi_boats[i] is hi_boat8:
        frames = 387
        adj = 1
        f = r'/Users/kellykai/Desktop/Flask_app/Static/hiboat8.mp4'
        color = 'blue'
        
    if hi_boats[i] is hi_boat9:
        frames = 144
        adj = 1
        f = r'/Users/kellykai/Desktop/Flask_app/Static/hiboat9.mp4'
        color = 'blue'
        
    if hi_boats[i] is hi_boat10:
        frames = 3023
        adj = 1
        f = r'/Users/kellykai/Desktop/Flask_app/Static/hiboat10.mp4'
        color = 'blue'

        
    x = list(hi_boats[i].lon)
    fig, ax = plt.subplots(figsize=(8,6))
    #fig = plt.figure()
    #l = [1]
    
    lines = plt.plot([],'o', c = color)
    line = lines[0]
    

    #other setup 
    countries = gpd.read_file(  
         gpd.datasets.get_path("naturalearth_lowres"))
    countries[countries["name"] == "United States of America"].plot(color='#0B7530',
                                                     ax=ax)
    countries[countries["name"] == "Canada"].plot(color='#0B7530',
                                                     ax=ax)
    countries[countries["name"] == "Mexico"].plot(color='#0B7530',
                                                     ax=ax)
    ax.grid(b=True, alpha=0.5)
    plt.axis([-178, -150, 15, 32])

    #animate
    def animate(frame):
        #update plot 
        #l.append(int(frame*adj))
        
        y = list(hi_boats[i].lat)[int(frame*adj)]
        line.set_data((x[int(frame*adj)],y))
        if hi_boats[i] is hi_boat10 and hi_boat10.is_suspicious[int(frame*adj)] == 1 and hi_boat10.is_fishing[int(frame*adj)] == 1:
            line.set_color('red')
        elif hi_boats[i].is_fishing[frame*adj] != 0:
            line.set_color('green')
        else:
            line.set_color('blue')

    anim = FuncAnimation(fig, animate, frames = frames, interval = 20)
    video = anim.to_html5_video()
    html = display.HTML(video)
    display.display(html)
    writervideo = animation.FFMpegWriter(fps=60) 
    anim.save(f, writer=writervideo)
    plt.close()

In [269]:


frames = 3023
adj = 1
f = r'/Users/kellykai/Desktop/Flask_app/Static/hiboat10.mp4'
color = 'blue'


x = list(hi_boat10.lon)
fig, ax = plt.subplots(figsize=(8,6))
#fig = plt.figure()
#l = [1]

lines = plt.plot([],'o', c = color)
line = lines[0]


#other setup 
countries = gpd.read_file(  
     gpd.datasets.get_path("naturalearth_lowres"))
countries[countries["name"] == "United States of America"].plot(color='#0B7530',
                                                 ax=ax)
countries[countries["name"] == "Canada"].plot(color='#0B7530',
                                                 ax=ax)
countries[countries["name"] == "Mexico"].plot(color='#0B7530',
                                                 ax=ax)
ax.grid(b=True, alpha=0.5)
plt.axis([-178, -150, 15, 32])

#animate
def animate(frame):
    #update plot 
    #l.append(int(frame*adj))

    y = list(hi_boat10.lat)[int(frame*adj)]
    line.set_data((x[int(frame*adj)],y))
    if hi_boat10.is_suspicious[int(frame*adj)] == 1 and hi_boat10.is_fishing[int(frame*adj)] == 1:
        line.set_color('red')
    elif hi_boat10.is_fishing[frame*adj] != 0:
        line.set_color('green')
    else:
        line.set_color('blue')

anim = FuncAnimation(fig, animate, frames = frames, interval = 20)
video = anim.to_html5_video()
html = display.HTML(video)
display.display(html)
writervideo = animation.FFMpegWriter(fps=60) 
anim.save(f, writer=writervideo)
plt.close()

# ALASKA

In [395]:
#viewing data frame because of small issue below with prodiuing a graph that has a range from 170degrees east to 170 degrees west 
ak_eez

mmsi     timestamp  distance_from_shore  distance_from_port  \
0       8.681774e+13  1.343454e+09        163375.921875        284822.78125   
1       8.681774e+13  1.343459e+09        186770.687500        326702.87500   
2       8.681774e+13  1.343465e+09        220432.796875        373378.03125   
3       8.681774e+13  1.343466e+09        227053.890625        381247.78125   
4       8.681774e+13  1.343466e+09        228005.375000        382247.09375   
...              ...           ...                  ...                 ...   
427351  2.296758e+14  1.474424e+09        131924.765625        284864.90625   
427352  2.296758e+14  1.474426e+09        120765.406250        282329.75000   
427353  2.296758e+14  1.474426e+09        119863.648438        281569.03125   
427354  2.296758e+14  1.474427e+09        113213.828125        281106.96875   
427355  2.296758e+14  1.474427e+09        110568.531250        280971.75000   

        speed      course        lat  is_fishing           source gear_type  \
0        11.9  290.799988  50.182362         0.0  false_positives  trawlers   
1        11.7  294.299988  50.296593         0.0  false_positives  trawlers   
2        11.5  296.500000  50.435013         0.0  false_positives  trawlers   
3        11.3  294.700012  50.456142         0.0  false_positives  trawlers   
4        11.3  294.600006  50.457455         0.0  false_positives  trawlers   
...       ...         ...        ...         ...              ...       ...   
427351    9.4  133.399994  51.190495         0.0              gfw   unknown   
427352    8.9  129.399994  51.149391         0.0              gfw   unknown   
427353    8.4  136.199997  51.142899         0.0              gfw   unknown   
427354    7.9  131.399994  51.120838         0.0              gfw   unknown   
427355    7.8  128.699997  51.109276         0.0              gfw   unknown   

        is_suspicious         lon  
0                   0 -130.114365  
1                   0 -130.524872  
2                   0 -130.973099  
3                   0 -131.041519  
4                   0 -131.046005  
...               ...         ...  
427351              0 -130.152420  
427352              0 -130.079819  
427353              0 -130.068695  
427354              0 -130.029739  
427355              0 -130.007553  

[427356 rows x 12 columns]

In [357]:
#still trying to fix issue with graphing 
ak_eez.lon[1]>0

False

In [358]:
#change longitude to be graphable
lon = []
for i in range(len(ak_eez)): 
    if ak_eez.lon[i] > 0:
        lon.append(ak_eez.lon[i] - 360)
    else:
        lon.append(ak_eez.lon[i])
lon

[-130.114364624,
 -130.5248718262,
 -130.9730987549,
 -131.041519165,
 -131.046005249,
 -131.0489959717,
 -131.4976043701,
 -131.507232666,
 -131.9428710938,
 -131.9474945068,
 -131.9523010254,
 -131.9569244385,
 -131.96940612790002,
 -131.9725494385,
 -131.974105835,
 -131.9758148193,
 -132.4212341309,
 -132.4259338379,
 -132.8475189209,
 -133.7488861084,
 -134.203994751,
 -134.66926574709998,
 -136.9118041992,
 -137.3694000244,
 -137.8295440674,
 -138.7308654785,
 -138.7325439453,
 -138.7359466553,
 -138.73751831049998,
 -139.2070007324,
 -139.20863342290002,
 -139.2138977051,
 -139.2293548584,
 -139.2345428467,
 -140.1871948242,
 -140.1921386719,
 -140.1938018799,
 -140.19552612299998,
 -140.200592041,
 -141.2566680908,
 -141.7286071777,
 -142.2070465088,
 -144.077255249,
 -144.5694274902,
 -145.0370635986,
 -145.0961761475,
 -145.5486450195,
 -145.83430480959998,
 -145.83615112299998,
 -146.8709106445,
 -146.8761291504,
 -147.3813781738,
 -147.38845825200002,
 -147.8783569336,
 -14

In [370]:
# replacing lon column with new graphable lon column 
ak_eez.drop(columns = ['lon'], inplace = True)
ak_eez['lon'] = lon


-129.9851226807

In [374]:
#Aleutian Islands Habitat Conservation Area (AIHCA)
AIHCA_coord = {'lat': (50,55), 'lon': (170,-170)}
#list of suspicipous indices 
sus_ak = []
for i in range(len(ak_eez)):
    if 47<ak_eez.lat[i]<56 and -190<ak_eez.lon[i]<-170:
        sus_ak.append(i)
        
#creating list of suspicious indices and adding to dataframe         
is_suspicious = []        
for i in range(len(ak_eez)):
    if i in sus_ak:
        is_suspicious.append(1)
    else:
        is_suspicious.append(0)

ak_eez['is_suspicious'] = is_suspicious

In [375]:
#count to check for any is_suspicious and is_fishing instances
indices = []
for i in range(len(ak_eez)):
    if ak_eez.is_suspicious[i] == 1 and ak_eez.is_fishing[i] == 1:
        indices.append(i)
ak_eez.iloc[indices]

mmsi     timestamp  distance_from_shore  distance_from_port  \
124968  5.139444e+13  1.398650e+09        151237.828125        268457.56250   
124969  5.139444e+13  1.398650e+09        151237.828125        268457.56250   
124970  5.139444e+13  1.398650e+09        151237.828125        268457.56250   
124971  5.139444e+13  1.398650e+09        151237.828125        268457.56250   
124972  5.139444e+13  1.398650e+09        152196.796875        269452.09375   
124973  5.139444e+13  1.398651e+09        152196.796875        269452.09375   
124974  5.139444e+13  1.398651e+09        152196.796875        269452.09375   
124975  5.139444e+13  1.398651e+09        152196.796875        269452.09375   
124976  5.139444e+13  1.398651e+09        151917.312500        269557.84375   
136031  5.139444e+13  1.423431e+09        155970.515625        241400.37500   

        speed      course        lat  is_fishing               source  \
124968    8.4  135.000000  55.808815         1.0  dalhousie_longliner   
124969    8.4  133.699997  55.808567         1.0  dalhousie_longliner   
124970    8.4  131.800003  55.808281         1.0  dalhousie_longliner   
124971    8.6  131.199997  55.807987         1.0  dalhousie_longliner   
124972    8.6  127.400002  55.807285         1.0  dalhousie_longliner   
124973    8.6  131.500000  55.805725         1.0  dalhousie_longliner   
124974    9.0  130.699997  55.805241         1.0  dalhousie_longliner   
124975    8.6  130.199997  55.804993         1.0  dalhousie_longliner   
124976    8.6  127.300003  55.802837         1.0  dalhousie_longliner   
136031    7.2  129.199997  55.950142         1.0  dalhousie_longliner   

        gear_type  is_suspicious         lon  
124968  longlines              1 -170.018356  
124969  longlines              1 -170.017929  
124970  longlines              1 -170.017380  
124971  longlines              1 -170.016785  
124972  longlines              1 -170.015167  
124973  longlines              1 -170.011826  
124974  longlines              1 -170.010834  
124975  longlines              1 -170.010345  
124976  longlines              1 -170.005753  
136031  longlines              1 -170.571762

In [376]:
#splitting alaskan datframe by unique boat 
mmsi = []
for i in range(len(ak_eez)):
    if ak_eez.mmsi[i] not in mmsi:
        mmsi.append(ak_eez.mmsi[i])
len(mmsi)     

9

In [377]:
#split west coast dataframe by boat
ak_boat1, ak_boat2, ak_boat3,ak_boat4, ak_boat5, ak_boat6, ak_boat7, ak_boat8, ak_boat9 = [x for _, x in ak_eez.groupby(ak_eez['mmsi'])]
ak_boat1.reset_index(drop = True, inplace = True)
ak_boat2.reset_index(drop = True, inplace = True)
ak_boat3.reset_index(drop = True, inplace = True)
ak_boat4.reset_index(drop = True, inplace = True)
ak_boat5.reset_index(drop = True, inplace = True)
ak_boat6.reset_index(drop = True, inplace = True)
ak_boat7.reset_index(drop = True, inplace = True)
ak_boat8.reset_index(drop = True, inplace = True)
ak_boat9.reset_index(drop = True, inplace = True)

#making a list of the dataframes 
ak_boats = [ak_boat1, ak_boat2, ak_boat3,ak_boat4, ak_boat5, ak_boat6, ak_boat7, ak_boat8, ak_boat9]

#checking length to see if any are too long and need to remove port 
lens = []
for i in range(len(ak_boats)):
    lens.append(len(ak_boats[i]))
# all are fine, will leave port instances 
lens

[125519, 2379, 110510, 618, 728, 35301, 68401, 82004, 1896]

In [380]:

#ak boat 1, 3,6,7,8 is too long, too much port time, llets remove 
#if you want to remove port data 
port_list = []
for i in range(len(ak_boat1)):
    if ak_boat1.distance_from_shore[i] == 0.0 and ak_boat1.speed[i] == 0.0:
        port_list.append(i)
ak_boat1.drop(port_list, inplace = True)

port_list = []
for i in range(len(ak_boat3)):
    if ak_boat3.distance_from_shore[i] == 0.0 and ak_boat3.speed[i] == 0.0:
        port_list.append(i)
ak_boat3.drop(port_list, inplace = True)

port_list = []
for i in range(len(ak_boat6)):
    if ak_boat6.distance_from_shore[i] == 0.0 and ak_boat6.speed[i] == 0.0:
        port_list.append(i)
ak_boat6.drop(port_list, inplace = True)

port_list = []
for i in range(len(ak_boat7)):
    if ak_boat7.distance_from_shore[i] == 0.0 and ak_boat7.speed[i] == 0.0:
        port_list.append(i)
ak_boat7.drop(port_list, inplace = True)

port_list = []
for i in range(len(ak_boat8)):
    if ak_boat8.distance_from_shore[i] == 0.0 and ak_boat8.speed[i] == 0.0:
        port_list.append(i)
ak_boat8.drop(port_list, inplace = True)




#reset all indices 
ak_boat1.reset_index(drop = True, inplace = True)
ak_boat3.reset_index(drop = True, inplace = True)
ak_boat6.reset_index(drop = True, inplace = True)
ak_boat7.reset_index(drop = True, inplace = True)
ak_boat8.reset_index(drop = True, inplace = True)

In [381]:
#count to check for any is_suspicious and is_fishing instances

for i in range(len(ak_boats)):
    indicies = []
    for j in range(len(ak_boats[i])):
        if ak_boats[i].is_suspicious[j] == 1 and ak_boats[i].is_fishing[j] == 1:
            indicies.append(j)
    print(len(indicies))
#only boat 10 has instances of both

10
0
0
0
0
0
0
0
0


In [386]:
#just coat fishing 
for i in range(len(ak_boats)):
    indicies = []
    for j in range(len(ak_boats[i])):
        if ak_boats[i].is_fishing[j] == 1:
            indicies.append(j)
    print(len(indicies))

27765
1812
16314
451
542
11396
44527
8664
17


In [382]:
lens = []
for i in range(len(ak_boats)):
    lens.append(len(ak_boats[i]))
# all are fine, will leave port instances 
lens

[116470, 2379, 61470, 618, 728, 31840, 68190, 43274, 1896]

In [383]:
#plotting 
#lengths = [116470, 2379, 61470, 618, 728, 31840, 68190, 43274, 1896]
for i in range(len(ak_boats)): 
    
    if ak_boats[i] is ak_boat1:
        frames = 5000
        adj = 23
        f = r'/Users/kellykai/Desktop/Flask_app/Static/akboat1.mp4'
        color = 'blue'
    if ak_boats[i] is ak_boat2:
        frames = 1188
        adj = 2
        f = r'/Users/kellykai/Desktop/Flask_app/Static/akboat2.mp4'
        color = 'blue'
        
    if ak_boats[i] is ak_boat3:
        frames = 5000
        adj = 12
        f = r'/Users/kellykai/Desktop/Flask_app/Static/akboat3.mp4'
        color = 'blue'
    if ak_boats[i] is ak_boat4:
        frames = 618
        adj = 1
        f = r'/Users/kellykai/Desktop/Flask_app/Static/akboat4.mp4'
        color = 'blue'
    if ak_boats[i] is ak_boat5:
        frames = 728
        adj = 1
        f = r'/Users/kellykai/Desktop/Flask_app/Static/akboat5.mp4'
        color = 'blue'
        
    if ak_boats[i] is ak_boat6:
        frames = 3100
        adj = 10
        f = r'/Users/kellykai/Desktop/Flask_app/Static/akboat6.mp4'
        color = 'blue'
    if ak_boats[i] is ak_boat7:
        frames = 5000
        adj = 13
        f = r'/Users/kellykai/Desktop/Flask_app/Static/akboat7.mp4'
        color = 'blue'
    if ak_boats[i] is ak_boat8:
        frames = 4300
        adj = 10
        f = r'/Users/kellykai/Desktop/Flask_app/Static/akboat8.mp4'
        color = 'blue'
        
    if ak_boats[i] is ak_boat9:
        frames = 948
        adj = 2
        f = r'/Users/kellykai/Desktop/Flask_app/Static/akboat9.mp4'
        color = 'blue'

        
    x = list(ak_boats[i].lon)
    fig, ax = plt.subplots(figsize=(8,6))
    #fig = plt.figure()
    #l = [1]
    
    lines = plt.plot([],'o', c = color)
    line = lines[0]
    

    #other setup 
    countries = gpd.read_file(  
         gpd.datasets.get_path("naturalearth_lowres"))
    countries[countries["name"] == "United States of America"].plot(color='#0B7530',
                                                     ax=ax)
    countries[countries["name"] == "Canada"].plot(color='#0B7530',
                                                     ax=ax)
    countries[countries["name"] == "Mexico"].plot(color='#0B7530',
                                                     ax=ax)
    ax.grid(b=True, alpha=0.5)
    plt.axis([-190, -120, 47, 75])

    #animate
    def animate(frame):
        #update plot 
        #l.append(int(frame*adj))
        
        y = list(ak_boats[i].lat)[int(frame*adj)]
        line.set_data((x[int(frame*adj)],y))
        if ak_boats[i] is ak_boat5 and ak_boat5.is_suspicious[int(frame*adj)] == 1 and ak_boat5.is_fishing[int(frame*adj)] == 1:
            line.set_color('red')
        elif ak_boats[i] is ak_boat7 and ak_boat7.is_suspicious[int(frame*adj)] == 1 and ak_boat7.is_fishing[int(frame*adj)] == 1:
            line.set_color('red')
        elif ak_boats[i].is_fishing[frame*adj] != 0:
            line.set_color('green')
        else:
            line.set_color('blue')

    anim = FuncAnimation(fig, animate, frames = frames, interval = 20)
    video = anim.to_html5_video()
    html = display.HTML(video)
    display.display(html)
    writervideo = animation.FFMpegWriter(fps=60) 
    anim.save(f, writer=writervideo)
    plt.close()